In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import networkx as nx
import osmnx as ox
import folium


from utils import downcast


%matplotlib inline

sns.set(rc={'figure.figsize':(12, 8)})

x, y = 41.551401, -8.423002
distance = 3500

def add_routes_to_map(G, r):
    routes = []
    for i, e in r.iterrows():
        orig_node = ox.get_nearest_node(G, (e['began_lat'], e['began_long']))
        dest_node = ox.get_nearest_node(G, (e['end_lat'], e['end_long']))
        routes.append(nx.shortest_path(G, orig_node, dest_node, weight='length'))
    
    return routes

def add_pins(rows, m):
    for i, e in rows.iterrows():
        print(i)
        folium.Circle(
            radius=25,
            location=[e['latitude'], e['longitude']],
            color=e['color'],
            fill=False,
            fill_color=e['color'],
            popup=e['label']
        ).add_to(m)

In [2]:
flow = pd.read_csv('data/flow.csv', parse_dates=['creation_date', 'sunrise', 'sunset'])
flow = downcast(flow)
incidents = pd.read_csv('data/incidents.csv', parse_dates=['incident_date'])
incidents = downcast(incidents)
centralization = pd.read_csv('data/centralization.csv')
centralization = downcast(centralization)

In [3]:
roads = flow[['road_num', 'began_lat', 'end_lat', 'began_long', 'end_long']].iloc[1:9]

In [4]:
G = ox.graph_from_point((x, y), distance=distance, network_type='drive')

In [5]:
m = folium.Map(location=[x, y], tiles='Stamen Toner', zoom_start=13)

In [6]:
colors = {'major': 'crimson', 'moderate': 'orange', 'minor': 'yellow', 'undefined': 'purple', 'unknown delay': 'black'}
incidents['color'] = incidents['magnitude_of_delay_desc'].map(colors)

In [7]:
major = incidents[incidents['magnitude_of_delay_desc'] == 'major'].copy()

In [8]:
major = major.sort_values(by=['latitude', 'longitude'])

In [9]:
mag = {0: 'minor', 1: 'moderate', 2: 'major'}
centralization['label'] = centralization['gravity'].map(mag)
centralization['color'] = centralization['label'].map(colors)

In [10]:
centralization.head()

Unnamed: 0   latitude  longitude  gravity                  coordinates  \
0           0  41.551788   -8.42116        0  41.551790000000004,-8.42116   
1           1  41.531021   -8.46964        0            41.53102,-8.46964   
2           2  41.517288   -8.44452        1  41.51729,-8.444519999999999   
3           3  41.514069   -8.45438        1  41.514070000000004,-8.45438   
4           4  41.518219   -8.44936        1            41.51822,-8.44936   

                        road     incident_date  weekday  hour     label  \
0            avenida central  2018-07-24 14:58        1    14     minor   
1                       a 11  2018-07-24 14:58        1    14     minor   
2                       a 11  2018-07-24 16:01        1    16  moderate   
3  avenida ponte de covedelo  2018-07-24 16:47        1    16  moderate   
4                      en 14  2018-07-24 16:47        1    16  moderate   

    color  
0  yellow  
1  yellow  
2  orange  
3  orange  
4  orange

In [11]:
road_5 = centralization[centralization['road'] == 'avenida joão paulo ii']
road_5 = road_5.reset_index(drop=True)

In [12]:
road_5 = road_5[['latitude', 'longitude', 'gravity', 'weekday', 'hour', 'label', 'color']]

In [13]:
road_5.shape

(59, 7)

In [14]:
weekday = 1
hour = 17
events = road_5[(road_5['weekday'] == weekday) & (road_5['hour'] == hour)].copy()

In [15]:
events = events.reset_index(drop=True)

In [16]:
events.head()

latitude  longitude  gravity  weekday  hour     label    color
0  41.553661   -8.40441        0        1    17     minor   yellow
1  41.555290   -8.40029        1        1    17  moderate   orange
2  41.553150   -8.40532        2        1    17     major  crimson
3  41.553150   -8.40532        2        1    17     major  crimson
4  41.555290   -8.40029        1        1    17  moderate   orange

In [17]:
events['gravity'].mean()

1.1666666666666667

In [18]:
routes = add_routes_to_map(G, roads.iloc[4:5])

In [19]:
m = ox.plot_graph_folium(G, edge_width=0.5)

In [20]:
m = ox.plot_route_folium(G, routes[0], m, route_color='orange')

In [21]:
add_pins(events, m)

0
1
2
3
4
5


In [22]:
m